<a href="https://colab.research.google.com/github/tg-bomze/Jukebox_Colab/blob/master/Jukebox_Rus.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

<b><font color="black" size="+4">Jukebox: Модель генерации музыки</font></b>

<b><font color="black" size="+2">Базируется на:</font></b>

**GitHub репозиторий**: [Jukebox](https://github.com/openai/jukebox)

Статья: [Jukebox: A Generative Model for Music](https://arxiv.org/abs/2005.00341)

Авторство: **[OpenAI](https://openai.com/).**

<b><font color="black" size="+2">Колаб предоставил:</font></b>

Telegram: [@ShirMan](https://t.me/ShirMan).

<b><font color="black" size="+2">Пересобрал:</font></b>

GitHub: [@tg-bomze](https://github.com/tg-bomze),
Telegram: [@bomze](https://t.me/bomze),
Twitter: [@tg_bomze](https://twitter.com/tg_bomze).



```
Далее тыкай на кнопки (куда указывает красная стрелка) в каждом блоке поочередно. После нажатия дождись окончания выполнения.
```



In [0]:
#@title <b><font color="red" size="+3">←</font><font color="black" size="+3"> Проверяем выделенный графический процессор</font></b>

#@markdown *Для корректной работы Colab'a требуется графический процессор V100 или P100 с 16 Гб памяти. Выполните этот блок и посмотрите результат. Если же вам достался какой-либо другой, то сбросьте среду выполнения (сверху в меню **Runtime > Factory reset runtime**) и выполните этот блок заново. Повторяйте это до тех пор, пока не получите необходимый графический процессор.*
!nvidia-smi -L

GPU 0: Tesla P100-PCIE-16GB (UUID: GPU-f5e2441e-b371-d1d0-b19f-a21f7002623f)


In [0]:
#@title <b><font color="red" size="+3">←</font><font color="black" size="+3"> Монтируем гугл драйв</font></b>

#@markdown *Далее необходимо смонтировать ваш гугл драйв для сохранения промежуточных результатов. Для этого выполните этот блок. Вам будет дана ссылка, по которой необходимо перейти, авторизоваться и получить код доступа. Его нужно скопировать и вставить в пустое поле под ссылкой. Далее нажать Enter и дождаться окончания монтирования.*
from google.colab import drive
drive.mount('/content/gdrive')

In [0]:
#@title <b><font color="red" size="+3">←</font><font color="black" size="+3"> Устанавливаем Jukebox</font></b>

#@markdown *По окончанию выполнения этого блока появится кнопка "Restart Runtime" после красной надписи. Необходимо будет нажать на нее. В случае если кнопка не появилась или вы не смогли ее найти, то сделайте рестарт вручную (сверху в меню **Runtime > Restart runtime**). После рестарта продолжайте выполнять блоки дальше.*
!pip install git+https://github.com/openai/jukebox.git

In [0]:
#@title <b><font color="red" size="+3">←</font><font color="black" size="+3"> Подключаем необходимые библиотеки и выбираем модель</font></b>

#@markdown *Наилучший вариант "5b_lyrics", однако для него может быть недостаточно памяти. Если при выполнении этого блока вылезет ошибка, то попробуйте выбрать модель "1b_lyrics".*

import jukebox
import torch as t
import librosa
import os
from IPython.display import Audio
from jukebox.make_models import make_vqvae, make_prior, MODELS, make_model
from jukebox.hparams import Hyperparams, setup_hparams
from jukebox.sample import sample_single_window, _sample, \
                           sample_partial_window, upsample, \
                           load_prompts
from jukebox.utils.dist_utils import setup_dist_from_mpi
from jukebox.utils.torch_utils import empty_cache
rank, local_rank, device = setup_dist_from_mpi()

#@markdown *Время выполнения данного блока: ~6 минут.*

model = "5b_lyrics" #@param ["5b_lyrics", "1b_lyrics"]
hps = Hyperparams()
hps.sr = 44100
hps.n_samples = 3 if model=='5b_lyrics' else 8
# Specifies the directory to save the sample in.
# We set this to the Google Drive mount point.
hps.name = '/content/gdrive/My Drive/contSamples'
chunk_size = 16 if model=="5b_lyrics" else 32
max_batch_size = 3 if model=="5b_lyrics" else 16
hps.levels = 3
hps.hop_fraction = [.5,.5,.125]

vqvae, *priors = MODELS[model]
vqvae = make_vqvae(setup_hparams(vqvae, dict(sample_length = 1048576)), device)
top_prior = make_prior(setup_hparams(priors[-1], dict()), vqvae, device)

continuation = None

In [0]:
#@title <b><font color="red" size="+3">←</font><font color="black" size="+3"> Устанавливаем параметры выходного музыкального произведения</font></b>

#@markdown **Длительность музыкальной дорожки (*в секундах*):**
sample_length_in_seconds = 60 #@param {type:"slider", min:10, max:240, step:10}
hps.sample_length = (int(sample_length_in_seconds*hps.sr)//top_prior.raw_to_tokens)*top_prior.raw_to_tokens
assert hps.sample_length >= top_prior.n_ctx*top_prior.raw_to_tokens, f'Please choose a larger sampling rate'

#@markdown **Имя исполнителя (*доступные имена можно посмотреть [тут](https://jukebox.openai.com/). Перейдите по ссылке, введите в фильтр имя нужного исполнителя и если он имеется, то вставьте его имя ниже*):**
artist_name = "B.B. King" #@param {type:"string"}

#@markdown **Жанр музыкального произведения (*доступные жанры можно посмотреть [тут](https://jukebox.openai.com/). Перейдите по ссылке, введите в фильтр необходимый жанр и если он имеется, то вставьте его ниже*):**
genre_name = "Blues" #@param {type:"string"}

In [0]:
# <---= Для выполнения этого блока ткните на Play слева, но прежде
# вставьте ниже текст для вашего выходного музыкального произведения.
# Строку ниже (ту, где написано your_lyrics) и последнюю трогать нельзя!

your_lyrics = """
Oh lordy, trouble so hard
Oh lordy, trouble so hard,
Don't nobody know my troubles but God.
Don't nobody know my troubles but God.

Went down the hill, the other day.
My soul got happy and stayed all day.

Oh lordy, trouble so hard
Oh lordy, trouble so hard,
Don't nobody know my troubles but God.
"""

In [0]:
#@title <b><font color="red" size="+3">←</font><font color="black" size="+3"> Применяем введенные установки</font></b>
metas = [dict(artist = artist_name,
            genre = genre_name,
            total_length = hps.sample_length,
            offset = 0,
            lyrics = your_lyrics,
            ),
          ] * hps.n_samples
labels = [None, None, top_prior.labeller.get_batch_labels(metas, 'cuda')]
sampling_temperature = 0.96
lower_batch_size = 16
max_batch_size = 3 if model == "5b_lyrics" else 16
lower_level_chunk_size = 32
chunk_size = 16 if model == "5b_lyrics" else 32
sampling_kwargs = [dict(temp=.99, fp16=True, max_batch_size=lower_batch_size,
                        chunk_size=lower_level_chunk_size),
                    dict(temp=0.99, fp16=True, max_batch_size=lower_batch_size,
                         chunk_size=lower_level_chunk_size),
                    dict(temp=sampling_temperature, fp16=True, 
                         max_batch_size=max_batch_size, chunk_size=chunk_size)]

In [0]:
#@title <b><font color="red" size="+3">←</font><font color="black" size="+3"> Загружаем wav файл с входной песней в качестве примера</font></b>

#@markdown **Данный блок не обязательный.** *Если вы ничего не загрузите в качестве примера, то нейросеть сама придумает мотив песне.*
from google.colab import files

uploaded = files.upload()
for fn in uploaded.keys():
  print('User uploaded file "{name}" with length {length} bytes'.format(
      name=fn, length=len(uploaded[fn])))
 #@markdown *Сконвертировать MP3 в WAV можно по [этой ссылке](https://convertio.co/ru/mp3-wav/).* 
continuation = True
sample_hps = Hyperparams(dict(mode='primed', audio_file='/content/'+fn, prompt_length_in_seconds=14))

assert sample_hps.audio_file is not None
audio_files = sample_hps.audio_file.split(',')
duration = (int(sample_hps.prompt_length_in_seconds*hps.sr)//top_prior.raw_to_tokens)*top_prior.raw_to_tokens
x = load_prompts(audio_files, duration, hps)

In [0]:
#@title <b><font color="red" size="+3">←</font><font color="black" size="+3"> Производим предварительную генерацию</font></b>

#@markdown **Выполнение данного блока может занять достаточно долгое время. Для примера, 10-ти секундная музыкальная дорожка генерируется от 5 до 10 минут (*так вы можете посчитать, как долго будет производиться генерация в вашем случае*). По этой причине можно сходить и перекусить, пока нейросеть будет работать.**

if continuation:
  zs = top_prior.encode(x, start_level=0, end_level=len(priors), bs_chunks=x.shape[0])
else:
  zs = [t.zeros(hps.n_samples,0,dtype=t.long, device='cuda') for _ in range(len(priors))]
zs = _sample(zs, labels, sampling_kwargs, [None, None, top_prior], [2], hps)

In [0]:
#@markdown **Пример** (данный блок выполнять не нужно, а просто послушайте на что должен быть похож ваш результат)**:**

In [0]:
#@title <b><font color="red" size="+3">←</font><font color="black" size="+3"> Слушаем результат предварительной генерации</font></b>

#@markdown *Если ваш результат по качеству напоминает тот, что представлен выше, то значит все прошло хорошо и можно продолжать выполнение блоков. Наличие шумов не является проблемой, так как в дальнейшем мы повысим частоту дискретизации и результат будет более качественным.*
Audio(f'{hps.name}/level_2/item_0.wav')

In [0]:
#@title <b><font color="red" size="+3">←</font><font color="black" size="+3"> Производим основную генерацию</font></b>

#@markdown **Этот блок самый долгий. Минутную музыкальную дорожку он генерирует 8 часов, поэтому советую пойти вздремнуть, пока нейросеть будет работать.**

#@markdown *По окончанию выполнения блока Colab сам предложит вам скачать итоговый результат.*

if True:
  del top_prior
  empty_cache()
  top_prior=None
upsamplers = [make_prior(setup_hparams(prior, dict()), vqvae, 'cpu') for prior in priors[:-1]]
labels[:2] = [prior.labeller.get_batch_labels(metas, 'cuda') for prior in upsamplers]

zs = upsample(zs, labels, sampling_kwargs, [*upsamplers, top_prior], hps)

from google.colab import files
files.download(f'{hps.name}/level_1/item_1.wav')
files.download(f'{hps.name}/level_0/item_1.wav')

In [0]:
#@title <b><font color="red" size="+3">←</font><font color="black" size="+3"> Слушаем итоговый результат</font></b>
Audio(f'{hps.name}/level_0/item_1.wav')

In [0]:
#@title <b><font color="red" size="+3">←</font><font color="black" size="+3"> Очищаем все после себя</font></b>
del upsamplers
empty_cache()